# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [Apple iPhone 11](https://www.amazon.com/Apple-iPhone-11-64GB-Unlocked/dp/B07ZPKF8RG/ref=sr_1_13?dchild=1&keywords=iphone+12&qid=1631721363&sr=8-13) on amazon.

(2) Collect the top 10000 User Reviews of the film [Shang-Chi and the Legend of the Ten Rings](https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3) from IMDB.

(3) Collect all the reviews of the top 100 most popular software from [G2](https://www.g2.com/) or [Capterra](https://www.capterra.com/)

(4) Collect the abstracts of the top 10000 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(5) Collect all the information of the 904 narrators in the [Densho Digital Repository](https://ddr.densho.org/narrators/).

(6) Collect the top 10000 tweets by using hashtag ["#blacklivesmatter"](https://twitter.com/hashtag/blacklivesmatter) from Twitter. 



In [3]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import numpy as np
import itertools
import lxml.html as LH
url_link= 'https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3'
imdb_url_link = "https://www.imdb.com"
response = requests.get(url_link)
movies_soup = BeautifulSoup(response.text, "lxml")
movie_tags = movies_soup.find_all('a', attrs={'class': None})
movie_tags = [tag.attrs['href'] for tag in movie_tags 
              if tag.attrs['href'].startswith('/title') & tag.attrs['href'].endswith('/')]
movie_tags = list(dict.fromkeys(movie_tags))
movie_links = [imdb_url_link + tag + 'reviews' for tag in movie_tags]
def minMax(a):
      print(len(a))
      minposition = a.index(min(a))
      maxposition = a.index(max(a))
      return minposition, maxposition
def getReviews(soup):
    review_ratings = [tag.previous_element for tag in 
                           soup.find_all('span', attrs={'class': 'point-scale'})]
    if len(review_ratings) > 0:
      n_index, p_index = minMax(list(map(int, review_ratings)))
      review_list = soup.find_all('a', attrs={'class':'title'})
      reviews = ["https://www.imdb.com" + review['href'] for review in review_list]
      return reviews
    else:
      return None
def getSoup(url_link):
    response = requests.get(url_link)
    soup = BeautifulSoup(response.text, 'html.parser')
    return soup
def getReviewText(review_url):
    soup = getSoup(review_url)
    tag = soup.find('div', attrs={'class': 'text show-more__control'})
    return tag.getText()
def getUserName(review_url):    
    soup = getSoup(review_url)
    tag = soup.find('h3')
    return list(tag.children)[0].getText()
def getMovieTitle(review_url):    
    soup = getSoup(review_url)
    tag = soup.find('h1')
    return list(tag.children)[1].getText()
def getReviewPostedDate(review_url):    
    soup = getSoup(review_url)
    tag = soup.find('div', attrs={'class': 'display-name-date'})
    return list(tag.children)[1].getText()
def getRatings(review_url):    
    soup = getSoup(review_url)
    tag = soup.find('div', attrs={'class': 'ipl-ratings-bar'})
    return list(tag.children)[1].getText() if tag != None else list()
movie_soups = getSoup(movie_links[0])
movie_review = getReviews(movie_soups)
imdb_review_texts = [getReviewText(url) for url in movie_review]
user_Names = [getUserName(url) for url in movie_review]
user_ratings = [getRatings(url) for url in movie_review]
posted_dates = [getReviewPostedDate(url) for url in movie_review]
data = {'User_Name': user_Names,
        'Review_text': imdb_review_texts,
        'Review_posted_time': posted_dates,
        'Star': user_ratings}
df = pd.DataFrame(data)
df.head(25)

23


User_Name                                        Review_text  \
0           MartinHafer  I am not a big fan of the many, many Marvel fi...   
1           SnoopyStyle  Shaun (Simu Liu) and Katy (Awkwafina) are slac...   
2             boblipton  It was an okay movie. Simu Liu is the son of t...   
3        nogodnomasters  Shaun (Simu Liu) and Katy (Awkwafina) are park...   
4        Sleepin_Dragon  I was not expecting that, I had visions of a f...   
5               kosmasp  Of course I am just riffing off, teasing and m...   
6        classicsoncall  There seemed to be a lot of inconsistencies in...   
7         jboothmillard  The Marvel Cinematic Universe made a big impac...   
8        paul_haakonsen  Having seen the trailer for the 2021 Marvel ac...   
9           BA_Harrison  Martial arts meets the MCU in Shang-Chi and th...   
10            Gordon-11  I find this film very engaging from start to f...   
11      view_and_review  I've said this before about Marvel movies: the...   
12  TBJCSKCNRRQTreviews  It's been ten years since Shang-Chi(Liu, charm...   
13             neil-476  Shang-Chi leaves San Francisco with his friend...   
14       deloudelouvain  Without spoiling anything as this story stands...   
15            trashgang  Started like a mix between martial art and the...   
16                ksf-2  This is the story of ten rings, weapons, used ...   
17             jdesando  "The US government was almost toppled by a pre...   
18         lasttimeisaw  "Plain as day that Ying Li is pushing up daisi...   
19   Pjtaylor-96-138044  'Shang-Chi And The Legend Of The Ten Rings (20...   
20            FeastMode  Watch this in IMAX!!!! The entire movie has an...   
21              cherold  After a flashback, this movie jumps to a coupl...   
22           Edvis-1997  It was good. So far, it's in my top10 list of ...   
23         ThomasDrufke  Shang Chi was nowhere near the top of my most ...   
24           cricketbat  With no real concept of the character or the s...   

   Review_posted_time                 Star  
0     1 December 2021   \n\n\n\n\n\n7/10\n  
1        2 March 2022   \n\n\n\n\n\n8/10\n  
2   11 September 2021   \n\n\n\n\n\n6/10\n  
3   11 September 2021  \n\n\n\n\n\n10/10\n  
4    9 September 2021   \n\n\n\n\n\n9/10\n  
5   12 September 2021   \n\n\n\n\n\n9/10\n  
6    15 November 2021   \n\n\n\n\n\n7/10\n  
7   19 September 2021   \n\n\n\n\n\n6/10\n  
8    11 November 2021   \n\n\n\n\n\n9/10\n  
9    27 February 2022   \n\n\n\n\n\n5/10\n  
10   2 September 2021                   []  
11  14 September 2021   \n\n\n\n\n\n6/10\n  
12  10 September 2021   \n\n\n\n\n\n8/10\n  
13   8 September 2021   \n\n\n\n\n\n8/10\n  
14    6 December 2021   \n\n\n\n\n\n9/10\n  
15   14 November 2021   \n\n\n\n\n\n7/10\n  
16   21 February 2022   \n\n\n\n\n\n7/10\n  
17   9 September 2021                   []  
18   26 November 2021   \n\n\n\n\n\n7/10\n  
19   14 November 2021   \n\n\n\n\n\n7/10\n  
20   3 September 2021   \n\n\n\n\n\n9/10\n  
21   20 November 2021   \n\n\n\n\n\n8/10\n  
22     3 October 2021   \n\n\n\n\n\n7/10\n  
23    22 October 2021   \n\n\n\n\n\n9/10\n  
24   1 September 2021   \n\n\n\n\n\n7/10\n

In [15]:
!pip install selenium
!apt-get update 
!apt install chromium-chromedriver
from selenium.webdriver.support.ui import WebDriverWait as wait
from selenium.webdriver.common.by import By
from selenium import webdriver
import pandas as pd
import time

options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')
driver = webdriver.Chrome('chromedriver',options=options)
link = 'https://www.imdb.com/title/tt7286456/reviews?ref_=tt_urv'
title_array = []
review_array = []
driver.get(link)
for num in range(4):
  driver.find_element_by_class_name("ipl-load-more__button").click()
  time.sleep(5)
  listOfTitle = driver.find_elements(By.CLASS_NAME, "title")
  listOfReviews = driver.find_elements(By.CLASS_NAME, "text")
for ele, sub_ele in zip(listOfTitle, listOfReviews):
      title_array.append((ele.text).replace('\n',''))
      review_array.append(sub_ele.text)
df = pd.DataFrame(list(zip(title_array, review_array)), columns =['Title', 'Review'])
print("Length of data frame is {0}".format(len(df)))
df

Get:1 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Ign:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:4 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease [15.9 kB]
Hit:5 http://archive.ubuntu.com/ubuntu bionic InRelease
Ign:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Get:7 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release [696 B]
Hit:8 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Get:9 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release.gpg [836 B]
Get:10 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Get:11 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ Packages [80.4 kB]
Hit:12 http://ppa.launchpad.net/cran/

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning: find_element_by_class_name is deprecated. Please use find_element(by=By.CLASS_NAME, value=name) instead


Length of data frame is 125


Title  \
0                                  Good, if derivative   
1                                 great character work   
2                                     It's About a Man   
3                                             a mirror   
4                               Attention Must Be Paid   
..                                                 ...   
120                     Can you introduce me as Joker?   
121  Difficult, Challenging, Unfriendly Truths Abou...   
122                    Tremendous central performance.   
123                                  I think I get it.   
124                  Too good to be a comic book movie   

                                                Review  
0                                                       
1    Gotham is in dire difficulties like New York C...  
2    While I've watched many of the superhero movie...  
3    In many aspects, it is a mirror. For society, ...  
4    In a crumbling Gotham City, where the governme...  
..                                                 ...  
120                                                     
121  Uncomfortable close-ups with a broken man, str...  
122                                                     
123  An impressive movie that is hard to describe.\...  
124  As he walks the streets of Gotham City Arthur ...  

[125 rows x 2 columns]

# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming. 

(6) Lemmatization.

In [ ]:
import nltk
nltk.download()

NLTK Downloader
---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> d

Download which package (l=list; x=cancel)?
  Identifier> all
       | 
       | Downloading package abc to /root/nltk_data...
       |   Package abc is already up-to-date!
       | Downloading package alpino to /root/nltk_data...
       |   Package alpino is already up-to-date!
       | Downloading package biocreative_ppi to /root/nltk_data...
       |   Package biocreative_ppi is already up-to-date!
       | Downloading package brown to /root/nltk_data...
       |   Package brown is already up-to-date!
       | Downloading package brown_tei to /root/nltk_data...
       |   Package brown_tei is already up-to-date!
       | Downloading package cess_cat to /root/nltk_data...
       |   Package cess_cat is already up-to-date!
       | Down

True

**Removing Punctuation and Special Characters**

In [ ]:
import re

df['Reviews after Noise Removal'] = df['Review'].str.replace('[^\w\s]','')
df['Reviews after Noise Removal'] = df['Reviews after Noise Removal'].apply(lambda x: ''.join(re.sub(r"[^a-zA-Z0-9]+", ' ', charctr) for charctr in x ))

**Removing digits**

In [ ]:
df['After digits removal'] = df['Reviews after Noise Removal'].apply(lambda x: ''.join([i for i in x if not i.isdigit()]))

**Removing Stop words**

In [ ]:
from nltk.corpus import stopwords
stop = stopwords.words('english')
df['Stopwords Removal'] = df['After digits removal'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))

**Converting to lower case**

In [ ]:
df['Lower Case'] = df['Stopwords Removal'].apply(lambda x: " ".join(x.lower() for x in x.split()))
df

Title  ...                                         Lower Case
0    Outstanding movie with a haunting performance ...  ...  every movie comes truly makes impact joaquins ...
1                       Only certain people can relate  ...  this movie felt alone isolated truly relate yo...
2                             Perfect in every aspect.  ...  truly masterpiece the best hollywood film one ...
3                                        MASTERPIECE 😍  ...  joaquin phoenix gives tour de force performanc...
4                                     The Hype is real  ...  most time movies anticipated like end falling ...
..                                                 ...  ...                                                ...
120                                       Masterpiece!  ...  joker gift audiences i felt privileged person ...
121                               DARK AND DEPRESSING.  ...  dark depressing unsettling film haunting score...
122                                              Great  ...                                                   
123                               JOKER - IT'S ON YOU.  ...                                                   
124  Spare me the "best comic book movie ever" nons...  ...  it premiered last night sydney i lucky enough ...

[125 rows x 6 columns]

**Stemming**

In [ ]:
from nltk.stem import PorterStemmer
st = PorterStemmer()
df['After Stemming'] = df['Lower Case'].apply(lambda x: " ".join([st.stem(word) for word in x]))

**Lemmatization**

In [ ]:
from textblob import Word
import nltk
nltk.download('wordnet')

df['After Lemmatization'] = df['After Stemming'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()]))

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


**Saving to csv from data frame**

In [ ]:
df.to_csv('joker_reviews.csv', index=False)

# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

# **3.1 Parts of Speech Tagging**

In [ ]:
from nltk.tokenize import word_tokenize
pos = []
for sentence in df['Lower Case']:
  text = word_tokenize(sentence)
  pos.append(nltk.pos_tag(text))
pos

[[('every', 'DT'),
  ('movie', 'NN'),
  ('comes', 'VBZ'),
  ('truly', 'RB'),
  ('makes', 'VBZ'),
  ('impact', 'NN'),
  ('joaquins', 'NNS'),
  ('performance', 'NN'),
  ('scenography', 'NN'),
  ('brilliance', 'NN'),
  ('grotesque', 'NN'),
  ('haunting', 'VBG'),
  ('cringy', 'JJ'),
  ('hard', 'JJ'),
  ('watch', 'NN'),
  ('times', 'NNS'),
  ('mesmerizing', 'VBG'),
  ('wont', 'JJ'),
  ('blink', 'NN'),
  ('eye', 'NN'),
  ('watching', 'VBG'),
  ('tragic', 'JJ'),
  ('seriously', 'RB'),
  ('funny', 'JJ'),
  ('moments', 'NNS'),
  ('emotional', 'JJ'),
  ('rollercoaster', 'NN'),
  ('sometimes', 'RB'),
  ('multiple', 'JJ'),
  ('emotions', 'NNS'),
  ('poppingup', 'VBP'),
  ('time', 'NN'),
  ('far', 'RB'),
  ('typical', 'JJ'),
  ('actionriddled', 'VBD'),
  ('predictable', 'JJ'),
  ('superhero', 'NN'),
  ('movie', 'NN'),
  ('proper', 'JJ'),
  ('psychological', 'JJ'),
  ('thrillerdrama', 'NN'),
  ('single', 'JJ'),
  ('best', 'RBS'),
  ('character', 'NN'),
  ('development', 'NN'),
  ('i', 'NN'),
  ('eve

**Parts of Speech Count**

In [ ]:
from collections import Counter
counts = []
for tags in pos:
  count = Counter( tag for word,  tag in tags)
  counts.append(count)
counts

[Counter({'DT': 1,
          'JJ': 12,
          'NN': 17,
          'NNS': 4,
          'RB': 5,
          'RBS': 1,
          'VBD': 1,
          'VBG': 3,
          'VBN': 1,
          'VBP': 1,
          'VBZ': 2}),
 Counter({'CC': 1,
          'CD': 1,
          'DT': 3,
          'IN': 1,
          'JJ': 4,
          'NN': 13,
          'NNS': 2,
          'PRP': 2,
          'RB': 4,
          'RBR': 1,
          'VB': 2,
          'VBD': 2,
          'VBG': 1,
          'VBN': 1,
          'VBP': 4,
          'VBZ': 1}),
 Counter({'CC': 1,
          'CD': 1,
          'DT': 4,
          'EX': 1,
          'IN': 2,
          'JJ': 13,
          'JJR': 1,
          'JJS': 3,
          'MD': 2,
          'NN': 25,
          'NNS': 8,
          'PRP$': 2,
          'RB': 5,
          'RP': 1,
          'VB': 3,
          'VBD': 2,
          'VBG': 5,
          'VBP': 1,
          'VBZ': 5}),
 Counter({'DT': 3,
          'FW': 1,
          'IN': 1,
          'JJ': 7,
          'NN':

# 3.2 Constituency Parsing

In [ ]:
!pip install benepar

In [ ]:
%tensorflow_version 1.x
import benepar
benepar.download('benepar_en2')

TensorFlow 1.x selected.
[nltk_data] Downloading package benepar_en2 to /root/nltk_data...
[nltk_data]   Package benepar_en2 is already up-to-date!


True

In [ ]:
import spacy.cli
spacy.cli.download("en_core_web_sm")

✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')


In [ ]:
pip install tensorflow==1.14

In [ ]:
import benepar
parser = benepar.Parser("benepar_en2")
for sentence in df['Lower Case']:
  try:
    tree = parser.parse(sentence)
    print(tree)
  except:
    print("No Parse Tree")
    continue

Streaming output truncated to the last 5000 lines.
                                                          (NNP
                                                            industry))))
                                                    (NNP the)
                                                    (NNP two)
                                                    (NNP positives))
                                                  (NNP movie))
                                                (RB firstly)
                                                (NNP final)
                                                (NNP talk)
                                                (NNP show)
                                                (NNP scene))
                                              (VP (NNP littered)))
                                            (-RRB- though)
                                            (NP (NNP imperfections)))
                                          (PP
               

# **Dependency Parsing**

In [ ]:
import spacy
from spacy import displacy

nlp = spacy.load('en')
options = {'compact': True, 'font': 'Source Sans Pro', 'distance': 100}
for sentence in df['Lower Case']:
  doc = nlp(sentence)
  displacy.render(doc, style = 'dep', options=options, jupyter=True)

# **3.3  Named Entity Recognition**

In [ ]:
import en_core_web_sm
nlp = en_core_web_sm.load()

for sentence in df['Lower Case']:
  doc = nlp(sentence)
  for X in doc.ents:
    if X.text and X.label_:
      print([(X.text, X.label_)])

[('cringy hard watch times', 'ORG')]
[('one', 'CARDINAL')]
[('hollywood', 'GPE')]
[('one', 'CARDINAL')]
[('joaquin phoenix', 'PERSON')]
[('de force', 'ORG')]
[('phoenix', 'GPE')]
[('portrayal', 'NORP')]
[('first', 'ORDINAL')]
[('joaquin phoneix', 'PERSON')]
[('todd phillips', 'PERSON')]
[('phillips', 'PERSON')]
[('yesterday', 'DATE')]
[('venice', 'GPE')]
[('venice', 'GPE')]
[('nolans', 'NORP')]
[('y gloria', 'PERSON')]
[('hollywood', 'GPE')]
[('joaquin', 'PERSON')]
[('niro joaquin', 'PERSON')]
[('one', 'CARDINAL')]
[('years', 'DATE')]
[('joaquin phoenixs', 'PERSON')]
[('todd phillips', 'PERSON')]
[('disturbed', 'ORG')]
[('joaquin phoenix', 'PERSON')]
[('years ago', 'DATE')]
[('joaquin phoenix', 'PERSON')]
[('jack nicholson', 'PERSON')]
[('phoenix outstandingso', 'ORG')]
[('hour', 'TIME')]
[('hours', 'TIME')]
[('kinda justeh', 'PERSON')]
[('tens', 'CARDINAL')]
[('drama thriller', 'PERSON')]
[('ten', 'CARDINAL')]
[('year', 'DATE')]
[('year', 'DATE')]
[('phoenix', 'GPE')]
[('one', 'CARDIN

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 

In [1]:
'''
Constituency parsing/Syntatcical parsing is breaking a text into sub-texts/sub-phrases and this sub-text can be referred to as constituents.
This type of parsing defines the syntactical structure of a selected sentence. It consists of Sentence constituents, parts of speech tags and sentence words.
For example (S (NP (PRP i)) (ADVP (RB never))(VP (VBD left) (NP
      (NP (NN review) (NN title))(NP (JJ good) (JJ bad) (NN piece) (NNP garbage)))(SBAR (S (NP (PRP i)) (VP (VP (VBD registered) (NNP imdb) (NN account))
          (NNP vent) (NN opinion) (SBAR (S (NP (PRP i)) (VP (VBP want) (NP (NNS hours) (NN life)) (X (RB back))))))))))


Dependency parsing defines the grammatical structure of a selected sentence by considering each word as a node.
This type of parsing relies on dependency grammar. Here, each word is connected according to their relationships.
In the above one of the dependency parsing trees, we have intelligence, talents, metally, ill. In which talent - > integellient, they both are dependent.
'''

'\nConstituency parsing/Syntatcical parsing is breaking a text into sub-texts/sub-phrases and this sub-text can be referred to as constituents.\nThis type of parsing defines the syntactical structure of a selected sentence. It consists of Sentence constituents, parts of speech tags and sentence words.\nFor example (S (NP (PRP i)) (ADVP (RB never))(VP (VBD left) (NP\n      (NP (NN review) (NN title))(NP (JJ good) (JJ bad) (NN piece) (NNP garbage)))(SBAR (S (NP (PRP i)) (VP (VP (VBD registered) (NNP imdb) (NN account))\n          (NNP vent) (NN opinion) (SBAR (S (NP (PRP i)) (VP (VBP want) (NP (NNS hours) (NN life)) (X (RB back))))))))))\n\n\nDependency parsing defines the grammatical structure of a selected sentence by considering each word as a node.\nThis type of parsing relies on dependency grammar. Here, each word is connected according to their relationships.\nIn the above one of the dependency parsing trees, we have intelligence, talents, metally, ill. In which talent - > integell